# Sound effects and artificial reverberation

**Author:** Matias Etcheverry

**python version : 3.6**

In [86]:
import os
import struct
import sys
import wave
from copy import deepcopy
from math import ceil

import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import pyaudio
from tqdm import tqdm
from IPython.display import Audio, display

cmap = mpl.colormaps["tab10"].colors


## Functions to load and save the data

In [109]:
def load_music(file):
    return wave.open(file, "rb")


def play_music(file, chunk=1024):
    """
    Script from PyAudio doc
    """
    wf = load_music(file)
    p = pyaudio.PyAudio()
    stream = p.open(
        format=p.get_format_from_width(wf.getsampwidth()),
        channels=wf.getnchannels(),
        rate=wf.getframerate(),
        output=True,
    )
    data = wf.readframes(chunk)

    while data:
        stream.write(data)
        data = wf.readframes(chunk)

    stream.stop_stream()
    stream.close()
    p.terminate()


def nextpow2(x):
    assert x > 0
    p = ceil(np.log2(x))
    x_ = 2**p
    assert 2 ** (p - 1) < x <= x_
    return p, x_


def plot_sound(data, times, name="default_name", save=False):
    plt.figure(figsize=(30, 4))
    plt.fill_between(times, data)
    plt.xlim(times[0], times[-1])
    plt.xlabel("time (s)")
    plt.ylabel("amplitude")
    if save:
        plt.savefig(name + ".png", dpi=100)
    plt.show()


def load_sound(filename):
    current_path = os.getcwd()
    data_path = os.path.join(current_path, "sons")
    music = os.path.join(data_path, filename)
    wavefile = load_music(music)

    Fs = int(wavefile.getframerate())
    num_samples = int(wavefile.getnframes())
    data = wavefile.readframes(num_samples)
    data = struct.unpack("{n}h".format(n=num_samples), data)
    x = np.array(data)

    timestep = 1 / float(Fs)
    times = np.arange(len(x)) * timestep
    return music, x, wavefile.getparams(), Fs, times


def save_sound(data, params, filename):
    current_path = os.getcwd()
    data_path = os.path.join(current_path, "sons")
    music = os.path.join(data_path, filename)

    audio = data.astype("<h")
    with wave.open(music, "wb") as file:
        file.setparams(params)
        file.writeframes(audio.tobytes())

    return load_sound(filename)


## I - Phasing

Program the phasing effect with $a(n)$ following a sinusoidal variation of frequency $f_a$ between the values $amin$ and $amax$. (One may choose $a(n) = B + Asin(2\pi F_An/F_s)$ with $B = (amax + amin)/2$, $A = (amax - amin)/2$ and where $F_s$ is the sampling frequency).

In [91]:
def phase(x, fs, fa, amin, amax, p):
    A = (amax - amin) / 2
    B = (amax + amin) / 2
    an = B + A * np.sin(2 * np.pi * np.arange(len(x)) * fa / fs)
    x_rolled = np.roll(x, shift=p)
    x_rolled[:p] = 0
    return x + an * x_rolled


Test the effect with different values of $F_a$, $amax$ and $amin$ (remember that values of a close to $A = 1$ give the strongest effect)

In [92]:
song = "guitare"
music, x, params, Fs, times = load_sound(f"{song}.wav")
x_phased_high_fa = phase(x, Fs, fa=10000, amin=0, amax=1, p=8000)
x_phased_high_amplitude = phase(x, Fs, fa=10000, amin=-1, amax=3, p=8000)
x_phased_low_amplitude = phase(x, Fs, fa=10000, amin=1, amax=1.01, p=8000)
save_sound(x_phased_high_fa, params, f"phased_{song}_high_fa.wav")
save_sound(x_phased_high_amplitude, params, f"phased_{song}_high_amplitude.wav")
save_sound(x_phased_low_amplitude, params, f"phased_{song}_low_amplitude.wav")


('/home/matias/ASA/TP_Effets_Reverb_MVA-English/Sons/phased_guitare_low_amplitude.wav',
 array([ -1,  -3,  -3, ..., 378, 687, 864]),
 _wave_params(nchannels=1, sampwidth=2, framerate=22050, nframes=168072, comptype='NONE', compname='not compressed'),
 22050,
 array([0.00000000e+00, 4.53514739e-05, 9.07029478e-05, ...,
        7.62217687e+00, 7.62222222e+00, 7.62226757e+00]))

In [93]:
print("First, we display the original song: it is a solo guitar.")
display(Audio(f"sons/{song}.wav"))
print("Then, we can add a phase, very perceptible to the human ear.")
display(Audio(f"sons/phased_{song}_low_amplitude.wav"))
print(
    "This phase can appear with a very large frequency, which pollutes the original song."
)
display(Audio(f"sons/phased_{song}_high_fa.wav"))
print("Finally, we can increase the amplitude of the phase, so that it is saturated.")
display(Audio(f"sons/phased_{song}_high_amplitude.wav"))


First, we display the original song: it is a solo guitar.


Then, we can add a phase, very perceptible to the human ear.


This phase can appear with a very large frequency, which pollutes the original song.


Finally, we can increase the amplitude of the phase, so that it is saturated.


## II - Flanger

Write the filter recurrent equation:

The recurrent input-output equation is given by:
$$
y(n) = x(n) + a x(n - p(n))
$$
where $y(n)$, $x(n)$, $a$ and $p(n)$ are respectively the output, the input, the gain and the delay of the system at time instant n (given in number of samples).

In [105]:
def flange(x, fs, fp, pmin, pmax, a):
    A = (pmax - pmin) / 2
    B = (pmax + pmin) / 2
    pn = B + A * np.sin(2 * np.pi * np.arange(len(x)) * fp / fs)
    x_rolled = np.array([x[min(i + int(pn[i]), len(x) - 1)] for i in range(len(x))])
    return x + a * x_rolled


Program the phasing effect with $p(n)$ following a sinusoidal variation of frequency $f_p$ between the values $pmin$ and $pmax$. (One may choose $p(n) = B + Asin(2\pi f_pn=F_s)$ with $B = (pmax + pmin)/2$, $A = (pmax - pmin)/2$ and where $F_s$ is the sampling frequency).

In [107]:
song = "guitare"
music, x, params, Fs, times = load_sound(f"{song}.wav")
x_flanged = flange(x, Fs, fp=10, pmin=0, pmax=1000, a=1)
save_sound(x_flanged, params, f"phased_{song}_high_fa.wav")

print("First, we display the original song: it is a solo guitar.")
display(Audio(f"sons/{song}.wav"))
print("Then we add a kind of DJ remix.")
display(Audio(f"sons/phased_{song}_high_fa.wav"))


First, we display the original song: it is a solo guitar.


Then we add a kind of DJ remix.


Compute a value of $p_{200}$ which induces the lowest zero in the spectrum of the fixed system $(a = 1, p = p_{200})$ to be at a frequency $f_{200} = 200$ Hz). Deduce appropriate values for $pmax$ and $pmin$.

In [ ]:
a = 1
fp = 200
x_flanged = flange(x, Fs, fp=10, pmin=0, pmax=1000, a=1)


Test the effect with different values of $f_p$, $pmax$ and $pmin$ (remember that values of A close to $A = 1$ give the strongest effect)

In [114]:
song = "guitare"
music, x, params, Fs, times = load_sound(f"{song}.wav")
x_flanged_high_fp = flange(x, Fs, fp=1000, pmin=0, pmax=1000, a=1)
x_flanged_high_amplitude = flange(x, Fs, fp=10, pmin=0, pmax=1000, a=1)
x_flanged_low_amplitude = flange(x, Fs, fp=10, pmin=900, pmax=900.1, a=1)
save_sound(x_flanged_high_fp, params, f"flanged_{song}_high_fp.wav")
save_sound(x_flanged_high_amplitude, params, f"flanged_{song}_high_amplitude.wav")
save_sound(x_flanged_low_amplitude, params, f"flanged_{song}_low_amplitude.wav")


('/home/matias/ASA/TP_Effets_Reverb_MVA-English/Sons/flanged_guitare_low_amplitude.wav',
 array([-4, -4, -3, ...,  2,  1,  2]),
 _wave_params(nchannels=1, sampwidth=2, framerate=22050, nframes=168072, comptype='NONE', compname='not compressed'),
 22050,
 array([0.00000000e+00, 4.53514739e-05, 9.07029478e-05, ...,
        7.62217687e+00, 7.62222222e+00, 7.62226757e+00]))

In [116]:
print("First, we display the original song: it is a solo guitar.")
display(Audio(f"sons/{song}.wav"))
print("Then we add a kind of DJ remix.")
display(Audio(f"sons/flanged_{song}_high_amplitude.wav"))
print("We can increase the flanged effect, which becomes awful.")
display(Audio(f"sons/flanged_{song}_high_fp.wav"))
print(
    "Finally, we can decrease the amplitude of the delay. It is almost imperceptible."
)
display(Audio(f"sons/flanged_{song}_high_amplitude.wav"))


First, we display the original song: it is a solo guitar.


Then we add a kind of DJ remix.


We can increase the flanged effect, which becomes awful.


Finally, we can decrease the amplitude of the delay. It is almost imperceptible.


## III - Artificial reverberation

**What can be done to improve the realism of the model for a real room ?**

We can add higher order echoes, which may be significant for a small room. We can also add objects in the room, as they may bring different bouncing as well as modify the sound itself reflection.

**How many image sources would you have if you include second order echoes ?**

The source can bounce on the 6 walls, resulting in 6 images sources. These image sources can then bounce on the 5 remaining walls, resulting in $6\times5=30$ image sources. In the end, there are 36 image sources.

**To your opinion, is it necessary to include higher order echoes? justify your answer.**

There is no need to include higher order echoes. The sound dissipate itself quickly.

**Knowing that it is better that each comb filter cell (resp. all-pass filters) has the same reverberation time, give the gain $g_i$ which correspond to the following delays given in milliseconds (29.7 ms; 37.1 ms; 41.4 ms; 43.7 ms for comb filters and 96.83 ms and 32.92 ms for all pass filters) as a function of the reverberation time.**

We have:

* for a comb filter:
$$
g_i = 10^{-3\frac{m_iT}{T_r}}
$$

* for a comb filter:
$$
g_i = \left(  1 - \frac{7T}{T_r} \right)^{m_i}
$$

**Program and test your Schroeder reverberator on one of the given test signal for different room dimensions.**

In [257]:
def compute_gi(T, Tr, m, filter="comb"):
    if filter == "comb":
        return 10 ** (-3 * m * T / Tr)
    return (1 - 7 * T / Tr) ** m


def multiple_combs_filters(x, Tr, Fs, m=[29.7, 37.1, 41.4, 43.7]):
    total_output = np.zeros(len(x))
    for mi in m:
        ti = int(mi * 1e-3 * Fs)
        gi = compute_gi(1 / Fs, Tr, ti, filter="comb")
        comb_output = np.zeros(len(x) + ti)
        for i in range(ti, len(comb_output)):
            comb_output[i] = gi * comb_output[i - ti] - x[i - ti]
        total_output += comb_output[ti:]
    return total_output


def single_all_pass_filters(x, Tr, Fs, m):
    output = np.zeros(len(x))
    t = int(m * 1e-3 * Fs)
    g = compute_gi(1 / Fs, Tr, t, filter="all-pass")
    for i in range(t, len(x)):
        output[i] = -g * (x[i] - output[i - t]) + x[i - t]
    return output

def reverberator(x, Tr_comb, Tr_pass, Fs, m_comb, m_pass):
    x_reverb = multiple_combs_filters(x, Tr_comb, Fs, m_comb)
    for m in m_pass:
        x_reverb = single_all_pass_filters(x_reverb, Tr_pass, Fs, m)
    return x_reverb


In [292]:
song = "hand_clap_22mono"
Tr_pass = 1e-2
music, x, params, Fs, times = load_sound(f"{song}.wav")
x_reverb_large = reverberator(x, 0.2, Tr_pass, Fs, [29.7, 37.1, 41.4, 43.7], [96.83, 32.92])
x_reverb_small = reverberator(x, 0.9, Tr_pass, Fs, [29.7, 37.1, 41.4, 43.7], [96.83, 32.92])
x_reverb_best = reverberator(x, 1e-2, 4e-4, Fs, [29.7, 37.1, 41.4, 43.7], [96.83, 32.92])
save_sound(x_reverb_large, params, f"reverb_large_{song}.wav")
save_sound(x_reverb_small, params, f"reverb_small_{song}.wav")
save_sound(x_reverb_best, params, f"reverb_best_{song}.wav")

song = "guitare"
music, x, params, Fs, times = load_sound(f"guitare.wav")
x_reverb_best = reverberator(x, 1e-2, 4e-4, Fs, [29.7, 37.1, 41.4, 43.7], [96.83, 32.92])
save_sound(x_reverb_best, params, f"reverb_best_guitare.wav")

('/home/matias/ASA/TP_Effets_Reverb_MVA-English/Sons/reverb_best_guitare.wav',
 array([ 0,  0,  0, ...,  0,  0, -3]),
 _wave_params(nchannels=1, sampwidth=2, framerate=22050, nframes=168072, comptype='NONE', compname='not compressed'),
 22050,
 array([0.00000000e+00, 4.53514739e-05, 9.07029478e-05, ...,
        7.62217687e+00, 7.62222222e+00, 7.62226757e+00]))

Test the reverberator with dierent parameters (keeping in mind that coprime integer
values will lead to better results)

In [293]:
print("We first listen to the original song: a hand clap")
display(Audio(f"sons/hand_clap_22mono.wav"))
print("We try reverberation in a large room, with a small reverberation time.")
display(Audio(f"sons/reverb_large_hand_clap_22mono.wav"))
print("We can try on a ridiculously small room. The result doesn't look real.")
display(Audio(f"sons/reverb_small_hand_clap_22mono.wav"))
print("Best set of parameters so far:")
display(Audio(f"sons/reverb_best_hand_clap_22mono.wav"))

print("If we try on the guitare sample, the result is not good at all, as it quickly saturates. WARNING.")
display(Audio(f"sons/reverb_best_guitare.wav"))

We first listen to the original song: a hand clap


We try reverberation in a large room, with a small reverberation time.


We can try on a ridiculously small room. The result doesn't look real.


Best set of parameters so far:


If we try on the guitare sample, the result is not good at all, as it quickly saturates. WARNING.
